In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from torch import nn
import torch
from sklearn.metrics import mean_squared_error
from torch.utils.data import Dataset
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.model_selection import train_test_split
from torch.utils.data import DataLoader 
from torch.autograd import Variable
from tqdm import trange
from sklearn.metrics import mean_squared_error as mse
from hydroeval import evaluator, nse, kge, kgeprime
import time

import os
import ray
from ray import tune
from ray.air import session
from ray.air.checkpoint import Checkpoint
from ray.tune.schedulers import ASHAScheduler
torch.manual_seed(0)


In [34]:
## Read in the groudnwater and surface water valeus as X and the spring stage as Y
X = pd.read_csv("../data/processed/gw_stage.CSV",
                    parse_dates=['Datetime'],
                    index_col=['Datetime'])
print('Initial GW-SW Input Size: ',X.shape)
y = pd.read_csv("../data/processed/spring.CSV",
                    parse_dates=['datetime'],
                    index_col=['datetime'])
key_value = np.loadtxt("../data/processed/NameKey.CSV", dtype= "str", delimiter=",", skiprows=1)
stationNames = { k:v for k,v in key_value }
#print(stationNames)

##These are the wells that we are excluding from the analysis. 
#these wells are extremely close to the spring and neural networks will rely too heavily on them 
## as their values are nearly identical to the spring stage
tooClose=['8','9','10','12','13','14','25', '44', '61', '72']
print("These are the wells we are NOT using:") 
for i in tooClose:
    print(stationNames[i])

#Drop values exctremely close to the Sprin head
X.drop(X.columns[[8,9,10,12,13, 14, 25,44,61,72]], axis=1, inplace=True)
print("Excluded GW-SW Input Shape: ", X.shape)
X.rename(columns = stationNames, inplace = True)
dates=X.index
GW_SW=X.copy()

GW=X.iloc[:,:23]

SW=X.iloc[:,23:]

MET=pd.read_csv("../data/processed/DailyMet.CSV",
                parse_dates=['Datetime'],
                index_col=['Datetime'])




#Add Y columns as a separate column
y['timestamp']=y.index
y['timestamp']=pd.to_datetime(y['timestamp']).dt.tz_convert(None)
#=pd.to_datetime(['timestamp'], format='%Y-%m-%d %H:%M:%S')
y=y.rename(columns={'Gage_Height':'Wakulla', 'timestamp':'Datetime'})
y=y.set_index('Datetime')



#Create datasets for each of the neural network inputs

#### INPUT TYPE FEATURE SELECTION #######
#DF of Met data with Wakulla
met_df=MET.merge(y,how='inner', right_index=True, left_index=True)
met_names=met_df.columns[:-1]

#DF of GW DATA with Wakulla
gw_df=GW.merge(y,how='inner', right_index=True, left_index=True)
gw_names=gw_df.columns[:-1]

#DF of SW dATA with Wakulla
sw_df=SW.merge(y,how='inner', right_index=True, left_index=True)
sw_names=sw_df.columns[:-1]

#DF of MET + GW + Wakulla
GW_MET=pd.concat([GW, MET], axis =1)
met_gw_df=GW_MET.merge(y,how='inner', right_index=True, left_index=True)
met_gw_names=met_gw_df.columns[:-1]

#Df of MET + SW + Wakulla
SW_MET=pd.concat([SW, MET], axis =1)
met_sw_df=SW_MET.merge(y,how='inner', right_index=True, left_index=True)
met_sw_names=met_sw_df.columns[:-1]

#dF OF GW + SW + Wakula
gw_sw_df=GW_SW.merge(y,how='inner', right_index=True, left_index=True)
gw_sw_names=gw_sw_df.columns[:-1]

#DF of MET + GW + SW + Wakulla
GW_SW_MET=pd.concat([GW_SW, MET], axis=1)
gw_sw_met_df=GW_SW_MET.merge(y, how='inner', right_index=True, left_index=True)
gw_sw_met_names=gw_sw_met_df.columns[:-1]


########Process-Informed Feature Selection  Inputs########
## This code uses the prfix 'Concep' referring to 'Conceptual Understanding', 
## but these models corresponds to 'PI' prefix in  the paper

## DF of MET + GW Processes (Regional GW , Local GW, Coastal GW)
#this combines the met df with NWFWMD GW-7F (LEON CR-59)/S818, FGS- Sullivan Sink 1, and USGS-Lester Lewis/S788
Concep_MET_GW=pd.concat([MET, GW.iloc[:,15], GW.iloc[:,9], GW.iloc[:,0]], axis =1)
concep_met_gw_df=Concep_MET_GW.merge(y,how='inner', right_index=True, left_index=True)
concep_met_gw_names=concep_met_gw_df.columns[:-1]

### DF of MET + SW Processes (Lake infiltration, Natural Stream recharge, Stormwater Recharge)
## This df combine the met df with Lake Jackson - Miller Landing Road,BLACK CREEK @ CR 267 , and AMES SINK/S555
Concep_MET_SW=pd.concat([MET, SW.iloc[:,31], SW.iloc[:,22], SW.iloc[:,0]], axis =1)
concep_met_sw_df=Concep_MET_SW.merge(y,how='inner', right_index=True, left_index=True)
concep_met_sw_names=concep_met_sw_df.columns[:-1]


## DF of MET +GW+ SW Processes
###  (regional GW , Local GW, Coastal GW, Lake infiltration, Natural Stream recharge, Stormwater Recharge)
## This df combine the met df with NWFWMD GW-7F (LEON CR-59)/S818, FGS- Sullivan Sink 1, and USGS-Lester Lewis/S788
# and Lake Jackson - Miller Landing Road,BLACK CREEK @ CR 267 , and AMES SINK/S555
Concep_MET_GW_SW=pd.concat([MET, GW.iloc[:,15], GW.iloc[:,9], GW.iloc[:,0],SW.iloc[:,31], SW.iloc[:,22], SW.iloc[:,0]], axis =1)
concep_met_gw_sw_df=Concep_MET_GW_SW.merge(y,how='inner', right_index=True, left_index=True)
concep_met_gw_sw_names=concep_met_gw_sw_df.columns[:-1]





del(X,y,MET, GW,SW, GW_SW, GW_MET,SW_MET,GW_SW_MET,Concep_MET_GW, Concep_MET_SW, Concep_MET_GW_SW)


inputs_list=[met_df, gw_df, sw_df, met_gw_df, met_sw_df, gw_sw_df, gw_sw_met_df, 
             concep_met_gw_df, concep_met_sw_df,concep_met_gw_sw_df]
inputs_list_str=["MET", "GW","SW", "MET+ GW", "MET + SW", "GW + SW", "MET + GW + SW", 
                 "Concptual MET+ GW", "Concptual MET + SW","Concptual MET + GW + SW"]
inputnames_list=[met_names, gw_names, sw_names, met_gw_names, met_sw_names, gw_sw_names, gw_sw_met_names,
                concep_met_gw_names, concep_met_sw_names,concep_met_gw_sw_names]

Initial GW-SW Input Size:  (1101, 74)
NWFWMD-NITRATE 1
NWFWMD-NITRATE 2/S790
NWFWMD-NITRATE 4/S782
NWFWMD-NITRATE 6/S797
WAKULLA CORRECTIONAL INSTITUTE 1/S779
WAKULLA CONDUIT WELL@WEST OF HWY 61
NWFWMD GW-12F (RIVERSPRINGS MS)/S820
St  Marks River @ San Marcos de Apalachee S P 
WAKULLA RIVER AT BOAT TRAM
INDIAN SPRING RUN AT SR61
Excluded GW-SW Input Shape:  (1101, 64)


In [6]:
def scale_and_split(df):
    train, test = train_test_split(df, test_size=0.20, shuffle = False)
    train, val = train_test_split(train, test_size=0.15, shuffle = False)
    
    #Use train set as the sclaer to prevent data leakage
    X_scaler = StandardScaler().fit(train.iloc[:,:-1])
    train_Xscaled = X_scaler.transform(train.iloc[:,:-1])
    y_scaler= MinMaxScaler().fit(train.iloc[:,-1:])
    train_yscaled= y_scaler.transform(train.iloc[:,-1:])
    
    train_scaled = pd.DataFrame(np.append(train_Xscaled, train_yscaled,1), columns = df.columns[:])
 
    
    val_Xscaled = X_scaler.transform(val.iloc[:,:-1])
    val_yscaled= y_scaler.transform(val.iloc[:,-1:])
    val_scaled = pd.DataFrame(np.append(val_Xscaled, val_yscaled,1), columns = df.columns[:])
    
    test_Xscaled = X_scaler.transform(test.iloc[:,:-1])
    test_yscaled= y_scaler.transform(test.iloc[:,-1:])
    test_scaled = pd.DataFrame(np.append(test_Xscaled, test_yscaled,1), columns = df.columns[:])
    
    full_scaled_X=X_scaler.transform(df.iloc[:,:-1])
    full_scaled_y=y_scaler.transform(df.iloc[:,-1:])
    
    #return val_scaled,
    
    return train_scaled,  val_scaled, test_scaled, X_scaler, y_scaler, full_scaled_X, full_scaled_y

#Old one

def prepare_inputs_outputs(train, val, test, seq_len, inputs, output):   
    X_train, y_train = train[:len(train)-seq_len][inputs], train[[output]]
    X_val, y_val = val[:len(val)-seq_len][inputs], val[[output]]
    X_test, y_test = test[:len(test)-seq_len][inputs], test[[output]]
    #test[:len(test)-seq_len][inputs], test[[output]]
    return X_train, y_train, X_val, y_val, X_test, y_test,

'''
## Try New One
def prepare_inputs_outputs(train, val, test, seq_len, inputs, output):   
    X_train, y_train = train[inputs], train[output][seq_len-1:]
    X_val, y_val = val[:len(val)-seq_len][inputs], val[[output]]
    X_test, y_test = test[:len(test)-seq_len][inputs], test[[output]]
    return X_train, y_train, X_val, y_val, X_test, y_test
'''
###Theory here is that we take [seq_len] numbered away from trainX and pass it to Val_X 
#and same with val to Test set
#May not be necessary


class TimeSeries(Dataset):
    def __init__(self, X, y, seq_len):
        self.X = torch.tensor(np.array(X) ,dtype=torch.float32)
        self.y = torch.tensor(np.array(y) ,dtype=torch.float32)
        #self.column_input = column_input
        #self.column_output = column_output
        self.seq_len = seq_len
        
    #Gets the input sequence [X : X +seq_len], adn the corresponding, singular y+seq_len    
    def __getitem__(self,idx):
        return self.X[idx:idx+self.seq_len-1], self.y[idx+self.seq_len-1]

    def __len__(self):
        return len(self.X) - (self.seq_len-1)
    
    
def get_dataloader(X, y,seq_len, batch_size, shuffle_TF):
    return DataLoader(TimeSeries(X, y, seq_len),  batch_size, shuffle=shuffle_TF, drop_last = True)

In [21]:
# New Method which might make DeepExplainer Work. Same model but different syntax using nn.Sequential
class LSTM_FC_Drop_FC(nn.Module):
    def __init__(self, input_size, hidden_size, seq_len, drop_rate):
        super(LSTM_FC_Drop_FC, self).__init__()
        self.input_size = input_size #input size
        self.hidden_size = hidden_size #hidden state
        self.seq_len = seq_len #sequence length
        self.drop_rate = drop_rate
        self.lstm = nn.LSTM(input_size=input_size, hidden_size=hidden_size,
                    num_layers=1, batch_first=True)#lstm
        
        self.fc_layers= nn.Sequential(
            nn.Dropout(drop_rate),
            nn.Linear(hidden_size, hidden_size),

            nn.Linear(hidden_size, 1) #fully connected 1
        )
    
    def forward(self,x):   
        h_0 = Variable(torch.zeros(1, x.size(0), self.hidden_size)) #.to(device) #hidden state
        c_0 = Variable(torch.zeros(1, x.size(0), self.hidden_size)) #.to(device) #internal state
        # Propagate input through LSTM
        output, (hn, cn) = self.lstm(x, (h_0, c_0)) #lstm with input, hidden, and internal state
        #hn = hn.view(-1, self.hidden_size) #reshaping the data for Dense layer next
        out = self.fc_layers(hn)#first Dense
     
        return out

In [22]:
# Train model to take in the parameter block and whihc datfarme input we ude
def train_model(config):

    
    #if torch.cuda.is_available():  
        #device = "cuda:0" 
    #else:  
        #device = "cpu"  
    
    model = LSTM_FC_Drop_FC(config["input_size"], config["hidden_size"], 
                            config["seq_len"], config["drop_rate"])
    #model.to(device)
    
    loss_function = nn.MSELoss()
    optimizer = torch.optim.Adam(model.parameters(), lr=config['lr'])
    
    loaded_checkpoint = session.get_checkpoint()
    if loaded_checkpoint:
        with loaded_checkpoint.as_directory() as loaded_checkpoint_dir:
            model_state, optimizer_state = torch.load(os.path.join(loaded_checkpoint_dir, "checkpoint.pt"))
        model.load_state_dict(model_state)
        optimizer.load_state_dict(optimizer_state)
    
    ## Load  Data and get Train/Val dataloaders
    train, val, test, X_scaler, y_scaler, full_scaled_X, full_scaled_y = scale_and_split(config['df']) 
   
    X_train, y_train, X_val, y_val, X_test, y_test = prepare_inputs_outputs(train, val, test, 
                                                                        config['seq_len'],
                                                                        config['inputs'],
                                                                        config['outputs'][0])
    
    train_loader = get_dataloader(X_train, y_train, int(config['seq_len']),int(config['batch_size']), shuffle_TF=True)
    val_loader = get_dataloader(X_val, y_val, int(config['seq_len']),int(config['batch_size']), shuffle_TF=True)
    #test_loader = get_dataloader(X_test, y_test, parameters['seq_len'], parameters['batch_size_test'])
    #full_loader=get_dataloader(full_scaled_X, full_scaled_y, parameters['seq_len'], parameters['batch_size_test'])
    #Comment out Test and full becasue they are not needed yet
    
    #Training Loop
    for epoch in range(config["epochs"]): #loop over the dataset multiple times
        model.train()
        running_loss = 0.0
        epoch_steps = 0
        for i, data in enumerate(train_loader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs, labels = data
            #inputs, labels = inputs.to(device), labels.to(device)

            # zero the parameter gradients
            optimizer.zero_grad()

            # forward + backward + optimize
            outputs = model(inputs)
            loss = loss_function(outputs[-1,:,:], labels)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            epoch_steps += 1
            if i % 800 == 799:  # print every 800 mini-batches
                print("[%d, %5d] loss: %.3f" % (epoch + 1, i + 1,
                                                running_loss / epoch_steps))
                running_loss = 0.0

        # Validation loss
        val_loss = 0.0
        val_steps = 0
        total = 0
        correct = 0
        for i, data in enumerate(val_loader, 0):
            model.eval()
            with torch.no_grad():
                inputs, labels = data
                #inputs, labels = inputs.to(device), labels.to(device)

                outputs = model(inputs)
                loss = loss_function(outputs[-1,:,:], labels)
    
                val_loss += loss.cpu().numpy()
                val_steps += 1

        #os.makedirs("my_model", exist_ok=True)
        #torch.save((model.state_dict(), optimizer.state_dict()), "my_model/checkpoint.pt")
        #checkpoint = Checkpoint.from_directory("my_model")
        session.report({"loss": (val_loss / val_steps)})
    #print("Finished Training")
    #return model

    

In [23]:
def test_accuracy(best_result, model):
    
    #best_trained_model = LSTM_FC_Drop_FC(best_result.config["input_size"], 
     #                                    best_result.config["hidden_size"],
      #                                   best_result.config["seq_len"], 
        #                                 best_result.config["drop_rate"])
    
    device = "cuda:0" if torch.cuda.is_available() else "cpu"
    #best_trained_model.to(device)
    model.to(device)
    
    checkpoint_path = os.path.join(best_result.checkpoint.to_directory(), "checkpoint.pt")
    
    model_state, optimizer_state = torch.load(checkpoint_path)
    #best_trained_model.load_state_dict(model_state)



    train, val, test, X_scaler, y_scaler, full_scaled_X, full_scaled_y = scale_and_split(best_result.config['df']) 
   
    X_train, y_train, X_val, y_val, X_test, y_test = prepare_inputs_outputs(train, val, test, 
                                                                        best_result.config['seq_len'],
                                                                        best_result.config['inputs'],
                                                                        best_result.config['outputs'][0])
    
    #train_loader = get_dataloader(X_train, y_train, parameters['seq_len'],parameters['batch_size_train'])
    #val_loader = get_dataloader(X_val, y_val, parameters['seq_len'],parameters['batch_size_val'])
    test_loader = get_dataloader(X_test, y_test, best_result.config['seq_len'], best_result.config['batch_size'], shuffle_TF=False)
    #full_loader=get_dataloader(full_scaled_X, full_scaled_y, parameters['seq_len'], parameters['batch_size_test'])
    #Comment out Test and full becasue they are not needed yet
    

   
    test_label=[]
    test_pred=[]
    
    with torch.no_grad():
        for data in test_loader:
            inputs, labels = data
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            test_pred.append(outputs.squeeze().tolist())
            test_label.append(labels.squeeze().tolist())
    
    
    test_predictions_l = [item for sublist in test_pred for item in sublist]
    test_predictions=np.array(test_predictions_l).reshape(-1,1)

    test_real_y_l=[item for sublist in test_label for item in sublist]
    test_real_y=np.array(test_real_y_l).reshape(-1,1)

    test_predictions_scaled=y_scaler.inverse_transform(test_predictions)
    test_real_y_scaled=y_scaler.inverse_transform(test_real_y)
    
    test_nse=evaluator(nse, test_predictions_scaled, test_real_y_scaled)
    print("Test NSE:", test_nse)
    
    
    test_kge=evaluator(kge, test_predictions_scaled, test_real_y_scaled)[0][0]
    print("Test KGE:", test_kge)
   
    test_mse=mse(test_predictions_scaled, test_real_y_scaled)
    print("test  MSE: ", test_mse)
    return train_rmse, test_rmse, train_mae, test_mae, train_nse, test_nse, train_kge, test_kge, train_nnse, test_nnse


In [24]:
def plot_full_ts(best_result, model):
    
    train, val, test, X_scaler, y_scaler, full_scaled_X, full_scaled_y = scale_and_split(best_result.config['df']) 
   
    X_train, y_train, X_val, y_val, X_test, y_test = prepare_inputs_outputs(train, val, test, 
                                                                        best_result.config['seq_len'],
                                                                        best_result.config['inputs'],
                                                                        best_result.config['outputs'][0])
    full_loader=get_dataloader(full_scaled_X, full_scaled_y, best_result.config['seq_len'], best_result.config['batch_size'], shuffle_TF=False)
 
    
   
    device = "cuda:0" if torch.cuda.is_available() else "cpu"
    model.to(device)
    
    full_pred=[]
    full_label=[]
    for j, data in enumerate(full_loader):
                inputs, labels = data[0].to(device), data[1].to(device)
                #optimizer.zero_grad()
                labels_3D=labels.reshape(1,labels.shape[0],labels.shape[1])
                y_pred = model(inputs)
                full_pred.append(y_pred.squeeze().tolist())
                full_label.append(labels.squeeze().tolist())

    full_predictions_l = [item for sublist in full_pred for item in sublist]
    full_predictions=np.array(full_predictions_l).reshape(-1,1)

    full_real_y_l=[item for sublist in full_label for item in sublist]
    full_real_y=np.array(full_real_y_l).reshape(-1,1)

    full_predictions_scaled=y_scaler.inverse_transform(full_predictions)
    full_real_y_scaled=y_scaler.inverse_transform(full_real_y)
   
    seq_len=int(best_result.config['seq_len'])
    
    val_position=748-seq_len
    test_position=880-seq_len
    
    plt.figure(figsize=(10,6)) #plotting
    plt.plot(full_predictions_scaled, label="Modeled Stage")
    plt.plot(full_real_y_scaled, label='Measured Stage')
    
    plt.axvline(x=val_position, c='r', linestyle='--') #Cutoff of the Validation set
    plt.axvline(x=test_position, c='r', linestyle='--') #Cutoff of the test set
    plt.legend()
    plt.show()
    plt.close()
    print("Done!")

In [25]:
def main(num_samples=10, max_num_epochs=20, df=met_df, df_names=met_names):
    ###UPDATE CONFIG WITH TUNABLE PARAMETERS
    config = {'inputs':df_names,
              'input_size': len(df_names),
              'outputs':['Wakulla'],
              'seq_len': tune.randint(7,45), ## FIX
              'hidden_size': tune.choice([8,16,32,48,64,96,128]),
              'batch_size': tune.choice([4,8,12,16,24,32,64]),
              'lr':0.0005,
              'num_layers':1,   #Number of LSTM layers
              'drop_rate':0.3,
              'df': df,
              "epochs": tune.randint(2,20)
              }
    if torch.cuda.is_available():  
        device = "cuda:0" 
    else:  
        device = "cpu"  
    scheduler = ASHAScheduler(
        max_t=max_num_epochs,
        grace_period=4,
        reduction_factor=2)
    
    tuner = tune.Tuner(
        tune.with_resources(
            tune.with_parameters(train_model),
            resources={"cpu": 8}
        ),
        tune_config=tune.TuneConfig(
            metric="loss",
            mode="min",
            scheduler=scheduler,
            num_samples=num_samples,
        ),
        param_space=config,
    )
    
    results = tuner.fit()
    
    best_trial = results.get_best_result("loss", "min")
    
    print("Best trial config: {}".format(best_trial.config))
    print("Best trial final validation loss: {}".format(best_trial.metrics["loss"]))
    #print("Best trial final validation accuracy: {}".format(best_trial.last_result["accuracy"]))


    #best_model=train_model(best_trial.config)
    
    #test_accuracy(best_trial,best_model)
    #plot_full_ts(best_trial, best_model)


In [26]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=500, max_num_epochs=30, df = met_df, df_names= met_names)

2023-09-19 12:24:51,286	ERROR trial_runner.py:1062 -- Trial train_model_6c9eb_00048: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=5520, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['Precip', 'Max_Temp', 'Min_Temp', 'Mean_Temp', 'PET'], dtype='object'), 'input_size': 5, 'outputs': ['Wakulla'], 'seq_len': 25, 'hidden_size': 16, 'batch_size': 64, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, 'df':              Precip  Max_Temp  Min_Temp  Mean_Temp       PET   Wakulla
Datetime                                                              
2017-01-27  0.00000        58        39       48.5  3.189802  5.470909
2017-01-28  0.00000        51        38       44.5  2.403944  5.418021
2017-01-29  0.00000        63        38       50.5  3.755256  5.345313
2017-01-30  0.00000        65        31       48.0  4.131664  5.237917
2017-01-31  0.00000        75        35       55.0  5.095131  5.171563
...             ...       ...       ...        ...       ...       ...
2020-01-28  0.00000        67        36       51.5  4.295638  4.814896
2020-01-29  0.06000        53        35       44.0  2.776629  4.811146
2020-01-30  0.00000        65    

In [27]:

if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=20, df = gw_df, df_names= gw_names)

2023-09-19 13:15:41,985	ERROR trial_runner.py:1062 -- Trial train_model_920e3_00057: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=6360, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['USGS-LESTER LEWIS/S788', 'NWFWMD-BIKE TRAIL / NITRATE POT MAP/S795',
       'NWFWMD-BRADFORD BROOK DEEP/S793', 'NWFWMD-BRADFORD BROOK SHALLOW',
       'TOM BROWN TEST/S791', 'USGS-OLSON RD/S677',
       'NWFWMD-HQ FLORIDAN OBS/S704', 'USGS-LAKE JACKSON INTERMEDIATE/S706',
       'NWFWMD-NITRATE 5/S796', 'FGS - SULLIVAN SINK 1',
       'NWFWMD GW-2F-LZ (FT BRADEN)/S802', 'NWFWMD GW-3F-LZ (ANF FR-305)',
       'NWFWMD GW-4F-UZ (HWY27 DOT)', 'NWFWMD GW-5F (LEON CTY VFD)/S814',
       'NWFWMD GW-6F (MICC GREENWAY)/S816', 'NWFWMD GW-7F (LEON CR-59)/S818',
       'NWFWMD GW-5S (LEON CTY VFD)', 'NWFWMD GW-7S (LEON CR-59)',
       'NWFWMD GW-4F-LZ (HWY27 DOT)/S812', 'NWFWMD GW-2S (FT BRADEN)/S805',
       'NWFWMD GW-6S (MICC GREENWAY)', 'NWFWMD GW-2F-UZ (FT BRADEN)/S826',
       'NWFWMD GW-3F-UZ (ANF FR-305)'],
      dtype='object'), 'input_size': 23, 'outputs': ['Wakulla'], 'seq_len': 14, 'hidden_size': 128, 'batch_size': 4, 'lr': 0.0005, 'num_layers': 1,

In [28]:

if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=20, df = sw_df, df_names= sw_names)

2023-09-19 13:51:52,168	ERROR trial_runner.py:1062 -- Trial train_model_14292_00007: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=10956, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\r

Best trial config: {'inputs': Index(['AMES SINK/S555', 'MUNSON SLOUGH @ CAPITAL CIRCLE',
       'FORDS ARM TRIB@MERD', 'ALFORD ARM TRIB@BUCK', 'CENTRAL DD@ORANGE',
       'WEST DRAINAGE DITCH @ ROBERTS AVE', 'LAKE KANTURK OUTFALL',
       'LAKE LAFAYETTE OUTFALL', 'NE DD@MAHAN DR', 'PARK AV DD@ VIOLET - S100',
       'LAKE JACKSON FACILITY AKA 64/606',
       'NE Drainage Ditch @ Centerville and Blairstone',
       'Central Drainage Ditch @ Lake Bradford Road',
       'Boone Blvd Holding pond (City ID 700)', 'Still Creek at Capitola Rd',
       'Lake Iamonia Outfall @ Meridian Rd',
       'LEON HIGH SCHOOL STORMWATER INLET', 'LAKE BRADFORD',
       'ST MARKS RIVER @ TRAM RD', 'LAKE KINSALE OUTFALL',
       'LAKE MUNSON OUTFALL', 'MUNSON SLOUGH @ OAKRIDGE ROAD',
       'BLACK CREEK @ CR 267', 'LOST CREEK @ ARRAN RD (CR 368)',
       'BRADFORD BROOK @ AENON CHURCH ROAD', 'WEST DRAINAGE DITCH @ US 90',
       'ALFORD ARM TRIB@MICC', 'EAST DD@ADAMS ST', 'QUINCY CREEK@SR 267',
       'FISHE

In [29]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = met_gw_df, df_names= met_gw_names)

2023-09-19 14:35:16,361	ERROR trial_runner.py:1062 -- Trial train_model_018d6_00021: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=3296, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['USGS-LESTER LEWIS/S788', 'NWFWMD-BIKE TRAIL / NITRATE POT MAP/S795',
       'NWFWMD-BRADFORD BROOK DEEP/S793', 'NWFWMD-BRADFORD BROOK SHALLOW',
       'TOM BROWN TEST/S791', 'USGS-OLSON RD/S677',
       'NWFWMD-HQ FLORIDAN OBS/S704', 'USGS-LAKE JACKSON INTERMEDIATE/S706',
       'NWFWMD-NITRATE 5/S796', 'FGS - SULLIVAN SINK 1',
       'NWFWMD GW-2F-LZ (FT BRADEN)/S802', 'NWFWMD GW-3F-LZ (ANF FR-305)',
       'NWFWMD GW-4F-UZ (HWY27 DOT)', 'NWFWMD GW-5F (LEON CTY VFD)/S814',
       'NWFWMD GW-6F (MICC GREENWAY)/S816', 'NWFWMD GW-7F (LEON CR-59)/S818',
       'NWFWMD GW-5S (LEON CTY VFD)', 'NWFWMD GW-7S (LEON CR-59)',
       'NWFWMD GW-4F-LZ (HWY27 DOT)/S812', 'NWFWMD GW-2S (FT BRADEN)/S805',
       'NWFWMD GW-6S (MICC GREENWAY)', 'NWFWMD GW-2F-UZ (FT BRADEN)/S826',
       'NWFWMD GW-3F-UZ (ANF FR-305)', 'Precip', 'Max_Temp', 'Min_Temp',
       'Mean_Temp', 'PET'],
      dtype='object'), 'input_size': 28, 'outputs': ['Wakulla'], 'seq_len': 38, 'hidde

In [30]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = met_sw_df, df_names= met_sw_names)

2023-09-19 15:14:04,064	ERROR trial_runner.py:1062 -- Trial train_model_8853a_00016: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=10696, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\r

Best trial config: {'inputs': Index(['AMES SINK/S555', 'MUNSON SLOUGH @ CAPITAL CIRCLE',
       'FORDS ARM TRIB@MERD', 'ALFORD ARM TRIB@BUCK', 'CENTRAL DD@ORANGE',
       'WEST DRAINAGE DITCH @ ROBERTS AVE', 'LAKE KANTURK OUTFALL',
       'LAKE LAFAYETTE OUTFALL', 'NE DD@MAHAN DR', 'PARK AV DD@ VIOLET - S100',
       'LAKE JACKSON FACILITY AKA 64/606',
       'NE Drainage Ditch @ Centerville and Blairstone',
       'Central Drainage Ditch @ Lake Bradford Road',
       'Boone Blvd Holding pond (City ID 700)', 'Still Creek at Capitola Rd',
       'Lake Iamonia Outfall @ Meridian Rd',
       'LEON HIGH SCHOOL STORMWATER INLET', 'LAKE BRADFORD',
       'ST MARKS RIVER @ TRAM RD', 'LAKE KINSALE OUTFALL',
       'LAKE MUNSON OUTFALL', 'MUNSON SLOUGH @ OAKRIDGE ROAD',
       'BLACK CREEK @ CR 267', 'LOST CREEK @ ARRAN RD (CR 368)',
       'BRADFORD BROOK @ AENON CHURCH ROAD', 'WEST DRAINAGE DITCH @ US 90',
       'ALFORD ARM TRIB@MICC', 'EAST DD@ADAMS ST', 'QUINCY CREEK@SR 267',
       'FISHE

In [31]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = gw_sw_df, df_names= gw_sw_names)

2023-09-19 15:53:23,049	ERROR trial_runner.py:1062 -- Trial train_model_18375_00007: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=7800, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['USGS-LESTER LEWIS/S788', 'NWFWMD-BIKE TRAIL / NITRATE POT MAP/S795',
       'NWFWMD-BRADFORD BROOK DEEP/S793', 'NWFWMD-BRADFORD BROOK SHALLOW',
       'TOM BROWN TEST/S791', 'USGS-OLSON RD/S677',
       'NWFWMD-HQ FLORIDAN OBS/S704', 'USGS-LAKE JACKSON INTERMEDIATE/S706',
       'NWFWMD-NITRATE 5/S796', 'FGS - SULLIVAN SINK 1',
       'NWFWMD GW-2F-LZ (FT BRADEN)/S802', 'NWFWMD GW-3F-LZ (ANF FR-305)',
       'NWFWMD GW-4F-UZ (HWY27 DOT)', 'NWFWMD GW-5F (LEON CTY VFD)/S814',
       'NWFWMD GW-6F (MICC GREENWAY)/S816', 'NWFWMD GW-7F (LEON CR-59)/S818',
       'NWFWMD GW-5S (LEON CTY VFD)', 'NWFWMD GW-7S (LEON CR-59)',
       'NWFWMD GW-4F-LZ (HWY27 DOT)/S812', 'NWFWMD GW-2S (FT BRADEN)/S805',
       'NWFWMD GW-6S (MICC GREENWAY)', 'NWFWMD GW-2F-UZ (FT BRADEN)/S826',
       'NWFWMD GW-3F-UZ (ANF FR-305)', 'AMES SINK/S555',
       'MUNSON SLOUGH @ CAPITAL CIRCLE', 'FORDS ARM TRIB@MERD',
       'ALFORD ARM TRIB@BUCK', 'CENTRAL DD@ORANGE',
       'WEST D

In [32]:
## Memory issues with this one. Had to reduce from 500 samples to 400
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = gw_sw_met_df, df_names= gw_sw_met_names)

2023-09-19 16:35:24,787	ERROR trial_runner.py:1062 -- Trial train_model_06803_00002: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=3516, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['USGS-LESTER LEWIS/S788', 'NWFWMD-BIKE TRAIL / NITRATE POT MAP/S795',
       'NWFWMD-BRADFORD BROOK DEEP/S793', 'NWFWMD-BRADFORD BROOK SHALLOW',
       'TOM BROWN TEST/S791', 'USGS-OLSON RD/S677',
       'NWFWMD-HQ FLORIDAN OBS/S704', 'USGS-LAKE JACKSON INTERMEDIATE/S706',
       'NWFWMD-NITRATE 5/S796', 'FGS - SULLIVAN SINK 1',
       'NWFWMD GW-2F-LZ (FT BRADEN)/S802', 'NWFWMD GW-3F-LZ (ANF FR-305)',
       'NWFWMD GW-4F-UZ (HWY27 DOT)', 'NWFWMD GW-5F (LEON CTY VFD)/S814',
       'NWFWMD GW-6F (MICC GREENWAY)/S816', 'NWFWMD GW-7F (LEON CR-59)/S818',
       'NWFWMD GW-5S (LEON CTY VFD)', 'NWFWMD GW-7S (LEON CR-59)',
       'NWFWMD GW-4F-LZ (HWY27 DOT)/S812', 'NWFWMD GW-2S (FT BRADEN)/S805',
       'NWFWMD GW-6S (MICC GREENWAY)', 'NWFWMD GW-2F-UZ (FT BRADEN)/S826',
       'NWFWMD GW-3F-UZ (ANF FR-305)', 'AMES SINK/S555',
       'MUNSON SLOUGH @ CAPITAL CIRCLE', 'FORDS ARM TRIB@MERD',
       'ALFORD ARM TRIB@BUCK', 'CENTRAL DD@ORANGE',
       'WEST D

In [35]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = concep_met_gw_df, df_names= concep_met_gw_names)

2023-09-19 17:19:42,517	ERROR trial_runner.py:1062 -- Trial train_model_0a99a_00018: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=2840, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ra

Best trial config: {'inputs': Index(['Precip', 'Max_Temp', 'Min_Temp', 'Mean_Temp', 'PET',
       'NWFWMD GW-7F (LEON CR-59)/S818', 'FGS - SULLIVAN SINK 1',
       'USGS-LESTER LEWIS/S788'],
      dtype='object'), 'input_size': 8, 'outputs': ['Wakulla'], 'seq_len': 37, 'hidden_size': 128, 'batch_size': 4, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, 'df':              Precip  Max_Temp  Min_Temp  Mean_Temp       PET  \
Datetime                                                       
2017-01-27  0.00000        58        39       48.5  3.189802   
2017-01-28  0.00000        51        38       44.5  2.403944   
2017-01-29  0.00000        63        38       50.5  3.755256   
2017-01-30  0.00000        65        31       48.0  4.131664   
2017-01-31  0.00000        75        35       55.0  5.095131   
...             ...       ...       ...        ...       ...   
2020-01-28  0.00000        67        36       51.5  4.295638   
2020-01-29  0.06000        53        35       44.0  2.776629  

In [39]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = concep_met_sw_df, df_names= concep_met_sw_names)

2023-09-20 10:30:28,039	ERROR trial_runner.py:1062 -- Trial train_model_2e1aa_00005: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=15028, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\r

Best trial config: {'inputs': Index(['Precip', 'Max_Temp', 'Min_Temp', 'Mean_Temp', 'PET',
       'Lake Jackson - Miller Landing Road', 'BLACK CREEK @ CR 267',
       'AMES SINK/S555'],
      dtype='object'), 'input_size': 8, 'outputs': ['Wakulla'], 'seq_len': 40, 'hidden_size': 16, 'batch_size': 24, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, 'df':              Precip  Max_Temp  Min_Temp  Mean_Temp       PET  \
Datetime                                                       
2017-01-27  0.00000        58        39       48.5  3.189802   
2017-01-28  0.00000        51        38       44.5  2.403944   
2017-01-29  0.00000        63        38       50.5  3.755256   
2017-01-30  0.00000        65        31       48.0  4.131664   
2017-01-31  0.00000        75        35       55.0  5.095131   
...             ...       ...       ...        ...       ...   
2020-01-28  0.00000        67        36       51.5  4.295638   
2020-01-29  0.06000        53        35       44.0  2.776629   
202

In [38]:
if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=400, max_num_epochs=30, df = concep_met_gw_sw_df, df_names= concep_met_gw_sw_names)

2023-09-20 10:02:49,747	ERROR trial_runner.py:1062 -- Trial train_model_8f6fd_00136: Error processing event.
ray.exceptions.RayTaskError(ZeroDivisionError): ray::ImplicitFunc.train() (pid=20904, ip=127.0.0.1, repr=train_model)
  File "python\ray\_raylet.pyx", line 857, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 861, in ray._raylet.execute_task
  File "python\ray\_raylet.pyx", line 803, in ray._raylet.execute_task.function_executor
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\_private\function_manager.py", line 674, in actor_method_executor
    return method(__ray_actor, *args, **kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\util\tracing\tracing_helper.py", line 466, in _resume_span
    return method(self, *_args, **_kwargs)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\ray\tune\trainable\trainable.py", line 368, in train
    raise skipped from exception_cause(skipped)
  File "C:\Users\kcompare\Anaconda3\lib\site-packages\r

Best trial config: {'inputs': Index(['Precip', 'Max_Temp', 'Min_Temp', 'Mean_Temp', 'PET',
       'NWFWMD GW-7F (LEON CR-59)/S818', 'FGS - SULLIVAN SINK 1',
       'USGS-LESTER LEWIS/S788', 'Lake Jackson - Miller Landing Road',
       'BLACK CREEK @ CR 267', 'AMES SINK/S555'],
      dtype='object'), 'input_size': 11, 'outputs': ['Wakulla'], 'seq_len': 39, 'hidden_size': 96, 'batch_size': 8, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, 'df':              Precip  Max_Temp  Min_Temp  Mean_Temp       PET  \
Datetime                                                       
2017-01-27  0.00000        58        39       48.5  3.189802   
2017-01-28  0.00000        51        38       44.5  2.403944   
2017-01-29  0.00000        63        38       50.5  3.755256   
2017-01-30  0.00000        65        31       48.0  4.131664   
2017-01-31  0.00000        75        35       55.0  5.095131   
...             ...       ...       ...        ...       ...   
2020-01-28  0.00000        67        36

# Results 

## MET_DF Best Rsults
'input_size': 5, 'outputs': ['Wakulla'], 'seq_len': 25, 'hidden_size': 16, 'batch_size': 64, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, 'epochs': 5
                    
## GW_DF Best Results
'input_size': 23, 'outputs': ['Wakulla'], 'seq_len': 14, 'hidden_size': 128, 'batch_size': 4, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs:11 
                    
## SW_DF BEST RESULTS
input_size': 41, 'outputs': ['Wakulla'], 'seq_len': 11, 'hidden_size': 128, 'batch_size': 64, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 14

## MET_GW BEST RESULTS
'input_size': 28, 'outputs': ['Wakulla'], 'seq_len': 38, 'hidden_size': 64, 'batch_size': 24, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs:12

## MET_SW BEST RESULTS
input_size': 46, 'outputs': ['Wakulla'], 'seq_len': 35, 'hidden_size': 48, 'batch_size': 32, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 16

## GW_SW BEST RESULTS
'input_size': 64, 'outputs': ['Wakulla'], 'seq_len': 14, 'hidden_size': 64, 'batch_size': 24, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 19

## GW_SW_MET BEST RESULTS
'input_size': 69, 'outputs': ['Wakulla'], 'seq_len': 28, 'hidden_size': 64, 'batch_size': 24, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 17

-------------------
/Conceptual Models/
## Concep_MET_GW BEST RESULTS
 'input_size': 8, 'outputs': ['Wakulla'], 'seq_len': 37, 'hidden_size': 128, 'batch_size': 4, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 15
## Concep_MET_SW BEST RESULTS
'input_size': 8, 'outputs': ['Wakulla'], 'seq_len': 40, 'hidden_size': 16, 'batch_size': 24, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs: 8

## Concep_MET_GW_SW BEST RESULTS
'input_size': 11, 'outputs': ['Wakulla'], 'seq_len': 39, 'hidden_size': 96, 'batch_size': 8, 'lr': 0.0005, 'num_layers': 1, 'drop_rate': 0.3, epochs:16